In [1]:
import pandas as pd
import numpy as np
import os
import sumolib
import copy
from tqdm import tqdm
from datetime import datetime

In [2]:
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fmins = range(midnight, next_day, 300)
m = 105 # m ranges from 26 to 287
# sigtable 시작시각  : 현재시각 - 1200 = 08:25
# 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# 현재시각           : 08:45
present_time = fmins[m]
sigtable_start = fmins[m] - 1200
sim_start = fmins[m] - 900
sim_end = fmins[m] - 600
print(datetime.fromtimestamp(sigtable_start))
print(datetime.fromtimestamp(sim_start))
print(datetime.fromtimestamp(sim_end))
print(datetime.fromtimestamp(present_time))
net = sumolib.net.readNet('../../Data/networks/sn.net.xml')
inter_node = pd.read_csv('../../data/tables/inter_node.csv', index_col=0)

2024-01-05 08:25:00
2024-01-05 08:30:00
2024-01-05 08:35:00
2024-01-05 08:45:00


In [3]:
histid = pd.read_csv(f'../../Data/tables/histids/histids_{fmins[50]}.csv', index_col=0)
print(sorted(histid.node_id.unique()))

['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']


In [4]:
inter2node = dict(zip(inter_node['inter_no'], inter_node['node_id']))
node2inter = dict(zip(inter_node['node_id'], inter_node['inter_no']))
ch2pa = {'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'c30': 'i3'}
pa2ch = {'i0':['u00'], 'i1':[], 'i2':['u20'], 'i3':['c30', 'u30', 'u31', 'u32'], 'i6':[], 'i7':[], 'i8':[], 'i9':[]}
node_ids = sorted(inter_node.node_id.unique())
parent_ids = sorted(inter_node[inter_node.inter_type=='parent'].node_id.unique())
child_ids = sorted(inter_node[inter_node.inter_type=='child'].node_id.unique())

print(inter2node)
print(node2inter)
print(ch2pa)
print(pa2ch)
print(node_ids)
print(parent_ids)
print(child_ids)

{175: 'u00', 176: 'i1', 177: 'u20', 178: 'c30', 210: 'u60', 206: 'i7', 201: 'i8', 202: 'i9'}
{'i0': 175, 'u00': 175, 'i1': 176, 'i2': 177, 'u20': 177, 'i3': 178, 'u30': 178, 'u31': 178, 'u32': 178, 'c30': 178, 'i6': 210, 'u60': 210, 'i7': 206, 'i8': 201, 'i9': 202}
{'u00': 'i0', 'u20': 'i2', 'u30': 'i3', 'u31': 'i3', 'u32': 'i3', 'c30': 'i3'}
{'i0': ['u00'], 'i1': [], 'i2': ['u20'], 'i3': ['c30', 'u30', 'u31', 'u32'], 'i6': [], 'i7': [], 'i8': [], 'i9': []}
['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']
['i0', 'i1', 'i2', 'i3', 'i6', 'i7', 'i8', 'i9']
['c30', 'u00', 'u20', 'u30', 'u31', 'u32', 'u60']


In [5]:
print(fmins[m], datetime.fromtimestamp(fmins[m]))
histid = pd.read_csv(f'../../Data/tables/histids/histids_{fmins[m]}.csv', index_col=0)
match6 = pd.read_csv('../../Data/tables/matching/match6.csv', index_col=0)
histid = histid.reset_index(drop=True)
histid = histid.drop(columns=['inter_no'])
match6 = match6[['node_id', 'phase_no', 'ring_type', 'inc_edge', 'out_edge']].reset_index(drop=True)
display(histid)
display(match6)

1704411900 2024-01-05 08:45:00


node_id  start_unix  phas_A  phas_B  duration        inc_edge_A  \
0        i6  1704410420       1       1        24     -571542115_01   
1        i6  1704410420       1       2        19     -571542115_01   
2        i6  1704410420       2       2        39   571500535_02.18   
3        i6  1704410420       3       3        65  571511538_02.121   
4        i6  1704410420       4       4        23      571500585_02   
..      ...         ...     ...     ...       ...               ...   
215      i0  1704411630       3       4        26      571545870_02   
216      i0  1704411630       4       4        33      571510153_02   
217      i1  1704411670       1       1        37     -571542810_01   
218      i1  1704411670       2       2        93     -571542810_01   
219      i1  1704411670       3       3        40      571543469_02   

           out_edge_A        inc_edge_B    out_edge_B  
0        571500535_01               NaN           NaN  
1        571500535_01   571500535_02.18  571542115_01  
2        571511538_01   571500535_02.18  571542115_01  
3        571542115_01  571511538_02.121  571500585_01  
4        571511538_01      571500585_02  571500535_01  
..                ...               ...           ...  
215      571510153_01      571510153_02  571545870_01  
216      571500487_01      571510153_02  571545870_01  
217  -571542797_02.99   571542797_02.99  571542810_01  
218  -571542797_02.99     -571542810_01  571543469_01  
219  -571542797_02.99               NaN           NaN  

[220 rows x 9 columns]

node_id  phase_no ring_type       inc_edge       out_edge
0        i0         1         A  -571542797_02   571500487_01
1        i0         1         B  -571500487_01   571542797_02
2        i0         2         A  -571500487_01   571545870_01
3        i0         2         B  -571542797_02   571510153_01
4        i0         3         A   571545870_02   571510153_01
..      ...       ...       ...            ...            ...
111     u60         2         B   571500535_02  -571500535_02
112     u60         3         A            NaN            NaN
113     u60         3         B            NaN            NaN
114     u60         4         A            NaN            NaN
115     u60         4         B            NaN            NaN

[116 rows x 5 columns]

In [6]:
sorted(histid.node_id.unique())

['i0', 'i1', 'i2', 'i3', 'i6', 'i8', 'i9']

In [7]:
new_histids = []
for parent_id in parent_ids:
    for child_id in pa2ch[parent_id]:
        new_histid = histid.copy()[histid.node_id==parent_id]
        new_histid[['inc_edge_A', 'out_edge_A', 'inc_edge_B', 'out_edge_B']] = np.nan
        for i, row in new_histid.iterrows():
            phas_A = row.phas_A
            phas_B = row.phas_B
            new_match = match6[match6.node_id==child_id]
            Arow = new_match[(new_match.phase_no==phas_A) & (new_match.ring_type=='A')]
            if ~ Arow[['inc_edge', 'out_edge']].isna().all().all():
                inc_edge = Arow.iloc[0].inc_edge
                out_edge = Arow.iloc[0].out_edge
                new_histid.loc[i, ['inc_edge_A', 'out_edge_A']] = [inc_edge, out_edge]
            Brow = new_match[(new_match.phase_no==phas_B) & (new_match.ring_type=='B')]
            if ~ Brow[['inc_edge', 'out_edge']].isna().all().all():
                inc_edge = Brow.iloc[0].inc_edge
                out_edge = Brow.iloc[0].out_edge
                new_histid.loc[i, ['inc_edge_B', 'out_edge_B']] = [inc_edge, out_edge]
            new_histid.loc[i, 'node_id'] = child_id
        new_histids.append(new_histid)
histid_child = pd.concat(new_histids)
histids = pd.concat([histid.copy(), histid_child])
histids = histids.sort_values(by=['start_unix', 'node_id', 'phas_A', 'phas_B']).reset_index(drop=True)
display(histids)

node_id  start_unix  phas_A  phas_B  duration        inc_edge_A  \
0        i6  1704410420       1       1        24     -571542115_01   
1        i6  1704410420       1       2        19     -571542115_01   
2        i6  1704410420       2       2        39   571500535_02.18   
3        i6  1704410420       3       3        65  571511538_02.121   
4        i6  1704410420       4       4        23      571500585_02   
..      ...         ...     ...     ...       ...               ...   
411     u00  1704411630       3       4        26               NaN   
412     u00  1704411630       4       4        33               NaN   
413      i1  1704411670       1       1        37     -571542810_01   
414      i1  1704411670       2       2        93     -571542810_01   
415      i1  1704411670       3       3        40      571543469_02   

           out_edge_A        inc_edge_B    out_edge_B  
0        571500535_01               NaN           NaN  
1        571500535_01   571500535_02.18  571542115_01  
2        571511538_01   571500535_02.18  571542115_01  
3        571542115_01  571511538_02.121  571500585_01  
4        571511538_01      571500585_02  571500535_01  
..                ...               ...           ...  
411               NaN               NaN           NaN  
412               NaN               NaN           NaN  
413  -571542797_02.99   571542797_02.99  571542810_01  
414  -571542797_02.99     -571542810_01  571543469_01  
415  -571542797_02.99               NaN           NaN  

[416 rows x 9 columns]

In [8]:
node_ids = sorted(histids.node_id.unique())
nodes = [net.getNode(node_id) for node_id in node_ids]
print(node_ids)
print(nodes)

['c30', 'i0', 'i1', 'i2', 'i3', 'i6', 'i8', 'i9', 'u00', 'u20', 'u30', 'u31', 'u32']
[<junction id="c30"/>, <junction id="i0"/>, <junction id="i1"/>, <junction id="i2"/>, <junction id="i3"/>, <junction id="i6"/>, <junction id="i8"/>, <junction id="i9"/>, <junction id="u00"/>, <junction id="u20"/>, <junction id="u30"/>, <junction id="u31"/>, <junction id="u32"/>]


In [9]:
node2init = {}
for node in nodes:
    node_id = node.getID()
    conns = [(c.getJunctionIndex(), c) for c in node.getConnections()]
    conns = [c for c in conns if c[0] >= 0]
    conns = sorted(conns, key=lambda x: x[0])
    state = []
    for i, ci in conns:
        if ci.getTLLinkIndex() < 0:
            continue
        are_foes = False
        for j, cj in conns:
            if ci.getTo() == cj.getTo():
                continue
            if node.areFoes(i, j):
                are_foes = True
                break
        state.append('r' if are_foes else 'g')
    node2init[node_id] = state

# 어떤 연결과도 상충이 일어나지는 않지만, 신호가 부여되어 있는 경우에는 r을 부여
for _, row in histids.iterrows():
    node_id = row['node_id']
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        pass
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        pass
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                node2init[node_id][index] = 'r'
for node_id in node_ids:
    print(node_id, "".join(node2init[node_id]))

c30 rrrrrr
i0 grrrgrrrgrrrrrgrr
i1 grrrrrrgrr
i2 rrggrrr
i3 grrrrgrrrrgrrrrgrrrr
i6 grrrgrrrrgrrgrrr
i8 grrrrrrrgrrrgrrr
i9 rrrr
u00 ggggrgggg
u20 ggrggg
u30 ggggrggg
u31 ggggrggg
u32 gggggggr


In [10]:
print(present_time)
print(datetime.fromtimestamp(present_time))
sigtable = histids.copy()
sigtable['init_state'] = sigtable['node_id'].map(node2init)
sigtable['state'] = sigtable['init_state'].map(lambda x:''.join(x))
for i, row in sigtable.iterrows():
    node_id = row.node_id
    inc_edge_A = row.inc_edge_A
    inc_edge_B = row.inc_edge_B
    out_edge_A = row.out_edge_A
    out_edge_B = row.out_edge_B
    state = copy.deepcopy(node2init)[node_id]

    if pd.isna(inc_edge_A) or pd.isna(out_edge_A):
        continue
    else:
        inc_edge_A = net.getEdge(inc_edge_A)
        out_edge_A = net.getEdge(out_edge_A)
        for conn in inc_edge_A.getConnections(out_edge_A):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)

    if pd.isna(inc_edge_B) or pd.isna(out_edge_B):
        continue
    else:
        inc_edge_B = net.getEdge(inc_edge_B)
        out_edge_B = net.getEdge(out_edge_B)
        for conn in inc_edge_B.getConnections(out_edge_B):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        sigtable.at[i, 'state'] = ''.join(state)
sigtable = sigtable.dropna(subset='state')
sigtable = sigtable.reset_index(drop=True)
sigtable['phase_sumo'] = sigtable.groupby(['node_id', 'start_unix']).cumcount()
sigtable = sigtable[sigtable.start_unix >= sigtable_start]
sigtable = sigtable[['node_id', 'start_unix', 'phase_sumo', 'duration', 'state']]
sigtable = sigtable.sort_values(by=['start_unix', 'node_id'])
sigtable['start_dt'] = sigtable['start_unix'].apply(lambda x:datetime.fromtimestamp(x))
display(sigtable)

1704411900
2024-01-05 08:45:00


node_id  start_unix  phase_sumo  duration       state            start_dt
98       i2  1704410739           0        40     GGggGGG 2024-01-05 08:25:39
99       i2  1704410739           1        25     rrggrrr 2024-01-05 08:25:39
100      i2  1704410739           2        71     rrggrrr 2024-01-05 08:25:39
101      i2  1704410739           3        34     rrggGGG 2024-01-05 08:25:39
102     u20  1704410739           0        40      ggrggg 2024-01-05 08:25:39
..      ...         ...         ...       ...         ...                 ...
411     u00  1704411630           3        26   ggggrgggg 2024-01-05 08:40:30
412     u00  1704411630           4        33   ggggrgggg 2024-01-05 08:40:30
413      i1  1704411670           0        37  gGGGGGrgrr 2024-01-05 08:41:10
414      i1  1704411670           1        93  grrGGGGgrr 2024-01-05 08:41:10
415      i1  1704411670           2        40  grrrrrrgGG 2024-01-05 08:41:10

[318 rows x 6 columns]

In [11]:
sigtable[sigtable.node_id=='i6']

node_id  start_unix  phase_sumo  duration             state  \
106      i6  1704410760           0        24  grrrgGGGrgrrgrrr   
107      i6  1704410760           1        19  grrrgGGGrgrrgGGr   
108      i6  1704410760           2        39  grrrgrrrrgrrgGGG   
109      i6  1704410760           3        65  gGGGgrrrrgrrgrrr   
110      i6  1704410760           4        23  grrrgrrrrgGGgrrr   
159      i6  1704410930           0        24  grrrgGGGrgrrgrrr   
160      i6  1704410930           1        19  grrrgGGGrgrrgGGr   
161      i6  1704410930           2        39  grrrgrrrrgrrgGGG   
162      i6  1704410930           3        65  gGGGgrrrrgrrgrrr   
163      i6  1704410930           4        23  grrrgrrrrgGGgrrr   
212      i6  1704411100           0        24  grrrgGGGrgrrgrrr   
213      i6  1704411100           1        19  grrrgGGGrgrrgGGr   
214      i6  1704411100           2        39  grrrgrrrrgrrgGGG   
215      i6  1704411100           3        65  gGGGgrrrrgrrgrrr   
216      i6  1704411100           4        23  grrrgrrrrgGGgrrr   
273      i6  1704411270           0        24  grrrgGGGrgrrgrrr   
274      i6  1704411270           1        19  grrrgGGGrgrrgGGr   
275      i6  1704411270           2        39  grrrgrrrrgrrgGGG   
276      i6  1704411270           3        65  gGGGgrrrrgrrgrrr   
277      i6  1704411270           4        23  grrrgrrrrgGGgrrr   
338      i6  1704411440           0        24  grrrgGGGrgrrgrrr   
339      i6  1704411440           1        19  grrrgGGGrgrrgGGr   
340      i6  1704411440           2        39  grrrgrrrrgrrgGGG   
341      i6  1704411440           3        65  gGGGgrrrrgrrgrrr   
342      i6  1704411440           4        23  grrrgrrrrgGGgrrr   
393      i6  1704411609           0        24  grrrgGGGrgrrgrrr   
394      i6  1704411609           1        19  grrrgGGGrgrrgGGr   
395      i6  1704411609           2        39  grrrgrrrrgrrgGGG   
396      i6  1704411609           3        65  gGGGgrrrrgrrgrrr   
397      i6  1704411609           4        23  grrrgrrrrgGGgrrr   

               start_dt  
106 2024-01-05 08:26:00  
107 2024-01-05 08:26:00  
108 2024-01-05 08:26:00  
109 2024-01-05 08:26:00  
110 2024-01-05 08:26:00  
159 2024-01-05 08:28:50  
160 2024-01-05 08:28:50  
161 2024-01-05 08:28:50  
162 2024-01-05 08:28:50  
163 2024-01-05 08:28:50  
212 2024-01-05 08:31:40  
213 2024-01-05 08:31:40  
214 2024-01-05 08:31:40  
215 2024-01-05 08:31:40  
216 2024-01-05 08:31:40  
273 2024-01-05 08:34:30  
274 2024-01-05 08:34:30  
275 2024-01-05 08:34:30  
276 2024-01-05 08:34:30  
277 2024-01-05 08:34:30  
338 2024-01-05 08:37:20  
339 2024-01-05 08:37:20  
340 2024-01-05 08:37:20  
341 2024-01-05 08:37:20  
342 2024-01-05 08:37:20  
393 2024-01-05 08:40:09  
394 2024-01-05 08:40:09  
395 2024-01-05 08:40:09  
396 2024-01-05 08:40:09  
397 2024-01-05 08:40:09

In [12]:
# sigtable 시작시각  : 현재시각 - 1200 = 08:25
# 시뮬레이션 시작시각 : 현재시각 - 900 = 08:30
# 시뮬레이션 종료시각 : 현재시각 - 600 = 08:35
# 현재시각           : 08:45
print(datetime.fromtimestamp(sigtable_start))
print(datetime.fromtimestamp(sim_start))
print(datetime.fromtimestamp(sim_end))
print(datetime.fromtimestamp(present_time))


2024-01-05 08:25:00
2024-01-05 08:30:00
2024-01-05 08:35:00
2024-01-05 08:45:00


In [15]:
offsets = {}
asigtable_list = []
for node_id in sorted(sigtable.node_id.unique()):
    asigtable = sigtable.copy()[sigtable.node_id==node_id]
    df = asigtable.copy()
    lsbs = asigtable[asigtable['start_unix'] < sim_start]['start_unix'].max() # the last start_unix before sim_start
    offsets[node_id] = lsbs - sim_start
    asigtable = asigtable[(asigtable['start_unix'] < sim_end) & (asigtable['start_unix'] >= lsbs)]
    asigtable_list.append(asigtable)
sigtable = pd.concat(asigtable_list)

strings = ['<additional>\n']
for node_id, group in sigtable.groupby('node_id'):
    strings.append(f'    <tlLogic id="{node_id}" type="static" programID="{node_id}_prog" offset="{offsets[node_id]}">\n')
    for i, row in group.iterrows():
        duration = row.duration
        state = row.state
        strings.append(f'      <phase duration="{duration}" state="{state}"/>\n')
    strings.append('    </tlLogic>\n')
strings.append('</additional>')
strings = ''.join(strings)
# 저장
path_output = '../../Data/networks/sn.add.xml'
with open(path_output, 'w') as f:
    f.write(strings)

print(strings)

<additional>
    <tlLogic id="c30" type="static" programID="c30_prog" offset="-50">
      <phase duration="38" state="rrrrrr"/>
      <phase duration="39" state="GGGGGG"/>
      <phase duration="42" state="GGGGGG"/>
      <phase duration="21" state="GGGGGG"/>
      <phase duration="38" state="rrrrrr"/>
      <phase duration="39" state="GGGGGG"/>
      <phase duration="42" state="GGGGGG"/>
      <phase duration="21" state="GGGGGG"/>
      <phase duration="38" state="rrrrrr"/>
      <phase duration="39" state="GGGGGG"/>
      <phase duration="42" state="GGGGGG"/>
      <phase duration="21" state="GGGGGG"/>
    </tlLogic>
    <tlLogic id="i0" type="static" programID="i0_prog" offset="-50">
      <phase duration="40" state="gGGrgrrrgGGGGrgrr"/>
      <phase duration="42" state="grrGgrrrgrrrrGgrr"/>
      <phase duration="29" state="grrrgGGGgrrrrrgrr"/>
      <phase duration="26" state="grrrgGGrgrrrrrgGr"/>
      <phase duration="33" state="grrrgrrrgrrrrrgGG"/>
      <phase duration="40" st